In [1]:
import numpy as np
import matplotlib.pyplot as plt
import scipy.optimize
from astropy.io import fits
%matplotlib inline

# Galaxy rotation
## Keplerian motion
For an object (like a planet or a star) to be in a stable circular orbit, its centripetal force (the force pulling it inwards towards the center of its orbit) must be exactly equal to the gravitational force it is experiencing. In equations, this is $$\frac{mv^2}{r} = \frac{GmM(r)}{r^2},$$ where $r$ is the orbital radius, $m$ is the mass of the object, $M(r)$ is the mass of the body holding it in orbit as a function of radius.

![image_info](http://www.scienceline.ucsb.edu/images/earth_sun_bodydiagram.png)


For the Solar System, we have the Sun at the center that comprises almost all of the mass, so $M(r) = M_\odot$. We can then solve the above equation for the velocity to get $$v = \sqrt{\frac{GM_\odot}{r}}.$$ So the velocity will fall off over time according to $r^{-1/2}$.

_Exercise:_ Kepler's third law says that for orbital period $T$ in this type of system, $T^2 = k r^3$. How can you get this from what we just calculated? What is the constant $k$?

## Galactic rotation curves
Galaxies are not like solar systems though since they don't just contain one giant mass that dominates. The supermassive black holes at the centers of galaxies are large, but they are still only a fraction of a percent of the total mass of the galaxy. For instance, the Milky Way's black hole only weighs about 0.00003% of the total mass of the Milky Way. So the vast majority of the mass of the galaxy comes from all of the other "stuff" scattered throughout it, like stars and gas. This means the mass that is responsible for the centripetal force $M(r)$ actually changes as a function of radius, so we won't get our nice Keplerian orbit. So what does rotational velocity look like as a function of radius for galaxies?

![image_info](https://voyages.sdss.org/wp-content/uploads/2019/07/spectra-comparison.png)

We can observe the rotational velocities of stars and gas in other galaxies by pointing a spectrograph at them. Taking advantage of the Doppler effect, if a part of a galaxy is moving towards us or away from us, the wavelength of its light will be shifted accordingly, resulting in blueshifting or redshifting. By comparing the wavelengths of the emission or absorption features of the spectrum to what we expect them to be, we can calculate the line of sight velocity of the thing we are looking at. If we do this across a whole galaxy, we can build up what we call a _rotation curve_.

![image_info](http://w.astro.berkeley.edu/~mwhite/darkmatter/rotation.gif)

Interestingly, the rotation curve shoots up quickly and then remains flat at a constant value $v_{max}$ out as far as we can see. What does $M(r)$ have to be in order for this to happen? Let's solve our equation to find out: $$M(r) = \frac{v_{max}^2 r}{G}.$$

So the overall mass of the galaxy increases linearly as a function of radius, and we can tell how heavy a galaxy is by measuring its $v_{max}$. However, if you do this, you will get an mass that is significantly larger than you would get if you added up all the stars you can see. 

![image_info](http://www.astronomy.ohio-state.edu/~pogge/Ast162/Unit6/Images/RotCurve2.gif)

People first started noticing this weirdness in the 1930s (one notable person who brushed it aside is Jan Oort of Oort cloud fame), but it wasn't until the late 1970s that Vera Rubin proposed that the difference was due to some unseen "dark matter." Her precise measurements and new insight were some of the first evidence for dark matter and remain unrefutable today.

![image_info](https://cdn.jwa.org/sites/default/files/styles/scale_width_300px/public/mediaobjects/Rubin-Vera.jpg?itok=9WwjhMCl)


# Tully-Fisher relation
The Tully-Fisher relation (TFR) is a well-tested and extremely useful relationship for spiral galaxies that was first experimentally derived in the late 1970s. There are many definitions of it that are slightly different, but it essentially says that bigger spiral galaxies rotate faster, and in a very regular and predictable way. This trend allows us to infer the size of a spiral galaxy from its rotation speed (or vice versa) without knowing anything else about it. Today we are going to fit some galaxy rotation data to rederive the TFR. 

First, let's load in the data we need: a file from a galaxy survey called MaNGA that contains a bunch of information about ~6000 galaxies, and some velocity information I have prepared on them.

In [2]:
drp = fits.open('drpall-v2_5_3.fits')
data = np.load('MPL8-kinematics.npy')

FileNotFoundError: [Errno 2] No such file or directory: 'drpall-v2_5_3.fits'

We are going to be classifying how "big" a galaxy is by looking at how bright it is. the DRPall file we just loaded contains a bunch of properties of each galaxy, including how bright they are in various in various filter bands. These correspond to different colors:

![image info](https://asd.gsfc.nasa.gov/archive/galex/Documents/ERO_data_description_2_files/image038.jpg)

Here we are going to load the `r` band, which corresponds to what we see as red, and the `NUV` band, which corresponds to UV radiation just below what we can see. The total luminosity of a given galaxy is stored in a column of the DRPall FITS file called `NSA_ELPETRO_ABSMAG`. 

Breaking down the name of this column, `NSA` refers to the NASA Sloan Atlas, which is a catalog of many thousands of nearby galaxies that has information on the global properties of the galaxies derived from images and spectra taken by the Sloan Digital Sky Survey. `ELPETRO` refers to the elliptical Petrosian method, a method for adding up all of the light a galaxy is putting out. `ABSMAG` refers to the absolute magnitude, a metric often used by astronomers to describe how bright something is independent of distance (defined as the relative magnitude if the object was 10 pc away).

Within the `NSA_ELPETRO_ABSMAG` column, there are 7 channels that correspond to the 7 bands that are shown above, starting from `FUV` and going up to `z`. Pull out the `r` channel and the `NUV` channel for all galaxies.

We also mask data that is obviously bad (MaNGA assigns bad data a value of -9999 so we just remove everything that is below -25)

In [ ]:
r = ???
nuv = ???
r = np.ma.array(r, mask = r < -25)
nuv = np.ma.array(nuv, mask = nuv < -25)

## Color-magnitude diagrams
Now we are going to make something called a color-magnitude diagram. These are more famous for their uses with stars, but they are used in galaxy science very often as well. We are going to plot the `r` band magnitude on the `x` axis and the quantity `nuv-r` on the `y` axis. `nuv-r` ends up being a measure of galaxy color, but the reason isn't totally obvious.

To see why, let's consider a blue galaxy. Blue is between UV and red, so a blue galaxy should have around the same brightness in `nuv` and in `r`, so the difference between the two should be small. Now let's consider a red galaxy. Red is very far from UV, so the red galaxy should be much brighter in `r` than in `nuv`. If we plot a ton of galaxies along these axes, we end up with two groups of galaxies, usually called the "red sequence" (elliptical galaxies) and the "blue cloud" (spiral galaxies), with the "green valley" (dead spirals) in between:

![image_info](https://galaxyzooblog.files.wordpress.com/2013/10/cmd_all.png)

Now let's make it ourselves. We will have to change the window size of our plot to an appropriate size to see what is going on because of outlier data points.

In [ ]:
#plot r on the x axis vs nuv-r on the y axis
#set the x and y limits of your plot as well as the types of the markers so you can see the data well
???
plt.xlabel('r magnitude')
plt.ylabel('nuv - r')

Looking at the points this way is not necessarily the clearest, so let's try some other methods of data visualization. First, we'll make them into a 2D histogram, kind of like the picture above, then we'll try messing with transparency to improve our previous plot. 

In [ ]:
#make a 2D histogram of r on the x axis and nuv-r on the y axis
#set the range and number of bins so you can see the data well
plt.hist2d(???
plt.xlabel('r magnitude')
plt.ylabel('nuv - r')

In [ ]:
#remake your original plot but mess with marker size and alpha (transparency) so it looks better
???
plt.xlabel('r magnitude')
plt.ylabel('nuv - r')

Now that we can see the difference between the red sequence and the blue cloud in our data, let's make a cut in our data set so we only include the blue spiral galaxies so we can look at the TFR

In [ ]:
#pick a good threshold to split blue spirals and red ellipticals
blue = nuv-r < ???

## Rotational velocity
Now let's see what the rotational velocity for these galaxies looks like. We'll make histograms of the blue galaxies, restricting the range to see the data well.

In [ ]:
#make a histogram of the velocity data, picking the appropriate range and number of bins
vmax = ???
???

We can see there's a spike of bad data at `vmax = 0` so let's remove that, plus any data with unreasonable magnitude measurements

In [ ]:
good = (0 < vmax) & (r < -15) & (r > -25)
cut = good & blue
cut.sum()

Now we can finally plot out TFR. Choose your favorite plotting method from above and we will plot the (cut) `r` values vs. the log of the (cut) `vmax` values.

In [ ]:
#plot the cut r values vs. the log of the vmax values
???

## Fitting the data
The TFR is really most useful as a predictive tool. If you can observe how fast a galaxy is rotating, you can then tell how bright it should be. If we then observe the galaxy as having a certain luminosity from our perspective, we can then tell about how far away it is. So we want to get an equation for the TFR. To do this, we will fit a line to the data we just obtained using Numpy's `polyfit` function. All we have to do is give it a set of `x` and `y` coordinates and the degree of polynomial we want it to fit and it will spit out the best description of the data. Then we'll plot it on top of the data with Numpy's `polyval` function to evaluate the model.

In [ ]:
#use polyfit to fit a line to your TFR and print the results
fit = np.polyfit(???
print(fit)

In [ ]:
#plot the best fit line on top of the data points
???

#the x and y coordinates of the points that make up your best fit line
x = ???
y = ???
plt.plot(x,y,'r-')

# Galaxy rotation curves
But what if we want to fit a function that isn't a polynomial? We'll explore this by fitting a rotation curve to actual galaxy velocity data. First, let's load in the data. In the file `pv_ha.txt`, we have 3 columns full of measurements of a galaxy's hydrogen gas kinematics from a longslit spectrograph. 

![image_info](https://upload.wikimedia.org/wikipedia/commons/f/fa/Longslit_spectroscopy_example.png)

The first column is the radial coordinate of the measurement, the second is the velocity in km/s, and the third is the error on the velocity measurement. Let's load the data and plot it (with error bars).

In [ ]:
#load in the text file and get the different measurements
???

In [ ]:
#use plt.errorbar to make a plot of the data with error bars
plt.errorbar(???

Now comes the actual science part: what kind of function does it look like? It has to be something that flattens out to a single value after a period of time, and something that is symmetrical about the origin. We want to be able to modify both the position and stretch of this function on the left/right and up/down axes. 

Write a function that you think can adapt to this data. It should take in some radius and return a velocity. Once you have a function that you think might describe the data well, you can start to test it with Scipy's `curve_fit` function. This is like `polyfit` but it will take any function you give it, not just polynomials. All you need to do is feed it the function, the `x` and `y` values, and the errors on the `y` values (`sigma`).

In [ ]:
#write a function to describe the data and use curve_fit to fit it
def rotcurve(???):
    return ???

fit,cov = scipy.optimize.curve_fit(???
print(fit)

Once you have a fit, plot it on top of the data. Does it look like it describes the data well? Tweak your function as necessary.

When I fit the data, I get a much better fit to the left part of the data than the right part. Why is this? How can you cut the data to better describe the data you have left?

In [ ]:
#plot your best fit function on top of your data
???